# Preprocessor for image data - distribution rules

This notebook shows how to set distribution rules parameter for moving training and validation datasets to certain segments where training will be done.  How you distribute data may depend, for example, on how GPUs are attached to your database cluster.

The distribution rules parameter is part of the mini-batch preprocessor utility for image data:
* `training_preprocessor_dl()` for training datasets
* `validation_preprocessor_dl()` for validation datasets


## Table of contents

<a href="#distr">1. Setup distribution rules</a>

<a href="#pp_train">2. Run preprocessor for training image data</a>
<ul>
<a href="#pp_train2a">2a. Distribute to all segments</a>
    
<a href="#pp_train2b">2b. Distribute to segments on hosts with GPUs attached</a>

<a href="#pp_train2c">2c. Distribute to segments on a subset of hosts</a>

<a href="#pp_train2d">2d. Distribute to 1 segment only</a>

</ul>

<a href="#pp_val">3. Run preprocessor for validation image data</a>

In [28]:
%load_ext sql

The sql extension is already loaded. To reload it, use:
  %reload_ext sql


In [29]:
# Greenplum Database 5.x on GCP - via tunnel
%sql postgresql://gpadmin@localhost:8000/cifar_places
        
# PostgreSQL local
#%sql postgresql://fmcquillan@localhost:5432/madlib

u'Connected: gpadmin@cifar_places'

In [30]:
%sql select madlib.version();
#%sql select version();

 * postgresql://gpadmin@localhost:8000/cifar_places
1 rows affected.


[(u'MADlib version: 1.17-dev, git revision: rc/1.16-rc1-95-gc62dfe7, cmake configuration time: Tue Mar 17 16:53:55 UTC 2020, build type: RelWithDebInfo, build system: Linux-2.6.32-754.6.3.el6.x86_64, C compiler: gcc 4.4.7, C++ compiler: g++ 4.4.7',)]

<a id="distr"></a>
# 1.  Setup distribution rules

Here are different ways to set up distribution rules tables.

First get the GPU configuration in the cluster using the MADlib helper function `gpu_configuration`:

In [31]:
%%sql
DROP TABLE IF EXISTS host_gpu_mapping_tf;
SELECT * FROM madlib.gpu_configuration('host_gpu_mapping_tf');
SELECT * FROM host_gpu_mapping_tf ORDER BY hostname, gpu_descr;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
1 rows affected.
20 rows affected.


[(u'gpsix0', u'device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0'),
 (u'gpsix0', u'device: 1, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:05.0, compute capability: 6.0'),
 (u'gpsix0', u'device: 2, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:06.0, compute capability: 6.0'),
 (u'gpsix0', u'device: 3, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:07.0, compute capability: 6.0'),
 (u'gpsix1', u'device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0'),
 (u'gpsix1', u'device: 1, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:05.0, compute capability: 6.0'),
 (u'gpsix1', u'device: 2, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:06.0, compute capability: 6.0'),
 (u'gpsix1', u'device: 3, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:07.0, compute capability: 6.0'),
 (u'gpsix2', u'device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0'),
 (u'gpsix2', u'device: 1, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:05.0, compute capability: 6.0'),
 (u'gpsix2', u'device: 2, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:06.0, compute capability: 6.0'),
 (u'gpsix2', u'device: 3, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:07.0, compute capability: 6.0'),
 (u'gpsix3', u'device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0'),
 (u'gpsix3', u'device: 1, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:05.0, compute capability: 6.0'),
 (u'gpsix3', u'device: 2, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:06.0, compute capability: 6.0'),
 (u'gpsix3', u'device: 3, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:07.0, compute capability: 6.0'),
 (u'gpsix4', u'device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0'),
 (u'gpsix4', u'device: 1, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:05.0, compute capability: 6.0'),
 (u'gpsix4', u'device: 2, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:06.0, compute capability: 6.0'),
 (u'gpsix4', u'device: 3, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:07.0, compute capability: 6.0')]

Review the Greenplum segments in the `gp_segment_configuration` table:

In [32]:
%%sql
SELECT * FROM gp_segment_configuration ORDER BY dbid;

 * postgresql://gpadmin@localhost:8000/cifar_places
21 rows affected.


[(1, -1, u'p', u'p', u'n', u'u', 5432, u'gpsix0', u'gpsix0', u'/data/master/gpseg-1'),
 (2, 0, u'p', u'p', u'n', u'u', 40000, u'gpsix0', u'gpsix0', u'/data/primary0/gpseg0'),
 (3, 1, u'p', u'p', u'n', u'u', 40001, u'gpsix0', u'gpsix0', u'/data/primary1/gpseg1'),
 (4, 2, u'p', u'p', u'n', u'u', 40002, u'gpsix0', u'gpsix0', u'/data/primary2/gpseg2'),
 (5, 3, u'p', u'p', u'n', u'u', 40003, u'gpsix0', u'gpsix0', u'/data/primary3/gpseg3'),
 (6, 4, u'p', u'p', u'n', u'u', 40000, u'gpsix1', u'gpsix1', u'/data/primary0/gpseg4'),
 (7, 5, u'p', u'p', u'n', u'u', 40001, u'gpsix1', u'gpsix1', u'/data/primary1/gpseg5'),
 (8, 6, u'p', u'p', u'n', u'u', 40002, u'gpsix1', u'gpsix1', u'/data/primary2/gpseg6'),
 (9, 7, u'p', u'p', u'n', u'u', 40003, u'gpsix1', u'gpsix1', u'/data/primary3/gpseg7'),
 (10, 8, u'p', u'p', u'n', u'u', 40000, u'gpsix2', u'gpsix2', u'/data/primary0/gpseg8'),
 (11, 9, u'p', u'p', u'n', u'u', 40001, u'gpsix2', u'gpsix2', u'/data/primary1/gpseg9'),
 (12, 10, u'p', u'p', u'n', u'u', 40002, u'gpsix2', u'gpsix2', u'/data/primary2/gpseg10'),
 (13, 11, u'p', u'p', u'n', u'u', 40003, u'gpsix2', u'gpsix2', u'/data/primary3/gpseg11'),
 (14, 12, u'p', u'p', u'n', u'u', 40000, u'gpsix3', u'gpsix3', u'/data/primary0/gpseg12'),
 (15, 13, u'p', u'p', u'n', u'u', 40001, u'gpsix3', u'gpsix3', u'/data/primary1/gpseg13'),
 (16, 14, u'p', u'p', u'n', u'u', 40002, u'gpsix3', u'gpsix3', u'/data/primary2/gpseg14'),
 (17, 15, u'p', u'p', u'n', u'u', 40003, u'gpsix3', u'gpsix3', u'/data/primary3/gpseg15'),
 (18, 16, u'p', u'p', u'n', u'u', 40000, u'gpsix4', u'gpsix4', u'/data/primary0/gpseg16'),
 (19, 17, u'p', u'p', u'n', u'u', 40001, u'gpsix4', u'gpsix4', u'/data/primary1/gpseg17'),
 (20, 18, u'p', u'p', u'n', u'u', 40002, u'gpsix4', u'gpsix4', u'/data/primary2/gpseg18'),
 (21, 19, u'p', u'p', u'n', u'u', 40003, u'gpsix4', u'gpsix4', u'/data/primary3/gpseg19')]

Now JOIN the above 2 tables to build up various distribution rules, depending on your needs.

Build distribution rules table for 4 VMs:

In [33]:
%%sql
DROP TABLE IF EXISTS segments_to_use_4VMs;
CREATE TABLE segments_to_use_4VMs AS
  SELECT DISTINCT dbid, hostname FROM gp_segment_configuration JOIN host_gpu_mapping_tf USING (hostname)
  WHERE role='p' AND content>=0 AND hostname!='gpsix4';
SELECT * FROM segments_to_use_4VMs ORDER BY hostname, dbid;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
16 rows affected.
16 rows affected.


[(2, u'gpsix0'),
 (3, u'gpsix0'),
 (4, u'gpsix0'),
 (5, u'gpsix0'),
 (6, u'gpsix1'),
 (7, u'gpsix1'),
 (8, u'gpsix1'),
 (9, u'gpsix1'),
 (10, u'gpsix2'),
 (11, u'gpsix2'),
 (12, u'gpsix2'),
 (13, u'gpsix2'),
 (14, u'gpsix3'),
 (15, u'gpsix3'),
 (16, u'gpsix3'),
 (17, u'gpsix3')]

Build distribution rules table for 2 VMs:

In [34]:
%%sql
DROP TABLE IF EXISTS segments_to_use_2VMs;
CREATE TABLE segments_to_use_2VMs AS
  SELECT DISTINCT dbid, hostname FROM gp_segment_configuration JOIN host_gpu_mapping_tf USING (hostname)
  WHERE role='p' AND content>=0 AND (hostname='gpsix0' OR hostname='gpsix1');
SELECT * FROM segments_to_use_2VMs ORDER BY hostname, dbid;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
8 rows affected.
8 rows affected.


[(2, u'gpsix0'),
 (3, u'gpsix0'),
 (4, u'gpsix0'),
 (5, u'gpsix0'),
 (6, u'gpsix1'),
 (7, u'gpsix1'),
 (8, u'gpsix1'),
 (9, u'gpsix1')]

Build distribution rules table for 1 VM:

In [35]:
%%sql
DROP TABLE IF EXISTS segments_to_use_1VM;
CREATE TABLE segments_to_use_1VM AS
  SELECT DISTINCT dbid, hostname FROM gp_segment_configuration JOIN host_gpu_mapping_tf USING (hostname)
  WHERE role='p' AND content>=0 AND hostname='gpsix0';
SELECT * FROM segments_to_use_1VM ORDER BY hostname, dbid;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
4 rows affected.
4 rows affected.


[(2, u'gpsix0'), (3, u'gpsix0'), (4, u'gpsix0'), (5, u'gpsix0')]

Build distribution rules table for 1 segment:

In [36]:
%%sql
DROP TABLE IF EXISTS segments_to_use_1seg;
CREATE TABLE segments_to_use_1seg AS
  SELECT DISTINCT dbid, hostname FROM gp_segment_configuration JOIN host_gpu_mapping_tf USING (hostname)
  WHERE dbid=2;
SELECT * FROM segments_to_use_1seg ORDER BY hostname, dbid;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
1 rows affected.
1 rows affected.


[(2, u'gpsix0')]

<a id="pp_train"></a>
# 2.  Run preprocessor for training image data

Run the preprocessor to generate the packed output table on the segments that you want to use for training and validation.  The training data in our example is CIFAR-10 and is in table `image_data_train` and the validation data is in `image_data_val` .

<a id="pp_train2a"></a>
## 2a.  All segments

First distribute to all segments:

In [37]:
%%sql
DROP TABLE IF EXISTS image_data_train_packed, image_data_train_packed_summary;

SELECT madlib.training_preprocessor_dl('image_data_train',          -- Source table
                                        'image_data_train_packed',  -- Output table
                                        'y',                        -- Dependent variable
                                        'x',                        -- Independent variable
                                        NULL,                       -- Buffer size
                                        255,                        -- Normalizing constant
                                        NULL,                       -- Number of classes
                                        'all_segments'              -- Distribution rules
                                        );
SELECT * FROM image_data_train_packed_summary;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
1 rows affected.
1 rows affected.


[(u'image_data_train', u'image_data_train_packed', u'y', u'x', u'smallint', [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 2500, 255.0, 10, 'all_segments', 'all_segments')]

Check distribution:

In [38]:
%%sql
SELECT __dist_key__, x_shape, y_shape, buffer_id FROM image_data_train_packed ORDER BY __dist_key__;

 * postgresql://gpadmin@localhost:8000/cifar_places
20 rows affected.


[(0, [2500, 32, 32, 3], [2500, 10], 1),
 (1, [2500, 32, 32, 3], [2500, 10], 4),
 (2, [2500, 32, 32, 3], [2500, 10], 9),
 (3, [2500, 32, 32, 3], [2500, 10], 7),
 (4, [2500, 32, 32, 3], [2500, 10], 14),
 (5, [2500, 32, 32, 3], [2500, 10], 17),
 (6, [2500, 32, 32, 3], [2500, 10], 16),
 (7, [2500, 32, 32, 3], [2500, 10], 11),
 (9, [2500, 32, 32, 3], [2500, 10], 13),
 (12, [2500, 32, 32, 3], [2500, 10], 15),
 (14, [2500, 32, 32, 3], [2500, 10], 6),
 (19, [2500, 32, 32, 3], [2500, 10], 12),
 (21, [2500, 32, 32, 3], [2500, 10], 18),
 (27, [2500, 32, 32, 3], [2500, 10], 10),
 (28, [2500, 32, 32, 3], [2500, 10], 5),
 (29, [2500, 32, 32, 3], [2500, 10], 8),
 (33, [2500, 32, 32, 3], [2500, 10], 19),
 (34, [2500, 32, 32, 3], [2500, 10], 0),
 (55, [2500, 32, 32, 3], [2500, 10], 3),
 (56, [2500, 32, 32, 3], [2500, 10], 2)]

<a id="pp_train2b"></a>
## 2b.  All segments on hosts with GPUs

Now distribute to all segments on hosts with GPUs attached:

In [39]:
%%sql
DROP TABLE IF EXISTS image_data_train_packed, image_data_train_packed_summary;

SELECT madlib.training_preprocessor_dl('image_data_train',          -- Source table
                                        'image_data_train_packed',  -- Output table
                                        'y',                        -- Dependent variable
                                        'x',                        -- Independent variable
                                        NULL,                       -- Buffer size
                                        255,                        -- Normalizing constant
                                        NULL,                       -- Number of classes
                                        'gpu_segments'              -- Distribution rules
                                        );
SELECT * FROM image_data_train_packed_summary;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
1 rows affected.
1 rows affected.


[(u'image_data_train', u'image_data_train_packed', u'y', u'x', u'smallint', [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 2500, 255.0, 10, [2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21], [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19])]

Check distribution:

In [40]:
%%sql
SELECT __dist_key__, x_shape, y_shape, buffer_id FROM image_data_train_packed ORDER BY __dist_key__;

 * postgresql://gpadmin@localhost:8000/cifar_places
20 rows affected.


[(0, [2500, 32, 32, 3], [2500, 10], 1),
 (1, [2500, 32, 32, 3], [2500, 10], 4),
 (2, [2500, 32, 32, 3], [2500, 10], 9),
 (3, [2500, 32, 32, 3], [2500, 10], 7),
 (4, [2500, 32, 32, 3], [2500, 10], 14),
 (5, [2500, 32, 32, 3], [2500, 10], 17),
 (6, [2500, 32, 32, 3], [2500, 10], 16),
 (7, [2500, 32, 32, 3], [2500, 10], 11),
 (9, [2500, 32, 32, 3], [2500, 10], 13),
 (12, [2500, 32, 32, 3], [2500, 10], 15),
 (14, [2500, 32, 32, 3], [2500, 10], 6),
 (19, [2500, 32, 32, 3], [2500, 10], 12),
 (21, [2500, 32, 32, 3], [2500, 10], 18),
 (27, [2500, 32, 32, 3], [2500, 10], 10),
 (28, [2500, 32, 32, 3], [2500, 10], 5),
 (29, [2500, 32, 32, 3], [2500, 10], 8),
 (33, [2500, 32, 32, 3], [2500, 10], 19),
 (34, [2500, 32, 32, 3], [2500, 10], 0),
 (55, [2500, 32, 32, 3], [2500, 10], 3),
 (56, [2500, 32, 32, 3], [2500, 10], 2)]

<a id="pp_train2c"></a>
## 2c.  Segments on 2 hosts with GPUs

Now distribute to segments on 2 hosts with GPUs attached (if for some reason I need to do this):

For small datasets like in this example, buffer size is mainly determined by the number of segments in the database. For a Greenplum database with 2 segments, there will be 2 rows with a buffer size of 26. For PostgresSQL, there would be only one row with a buffer size of 52 since it is a single node database. For larger data sets, other factors go into computing buffers size besides number of segments. 

Review the output summary table:

In [41]:
%%sql
DROP TABLE IF EXISTS image_data_train_packed, image_data_train_packed_summary;

SELECT madlib.training_preprocessor_dl('image_data_train',          -- Source table
                                        'image_data_train_packed',  -- Output table
                                        'y',                        -- Dependent variable
                                        'x',                        -- Independent variable
                                        NULL,                       -- Buffer size
                                        255,                        -- Normalizing constant
                                        NULL,                       -- Number of classes
                                        'segments_to_use_2VMs'      -- Distribution rules
                                        );
SELECT * FROM image_data_train_packed_summary;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
1 rows affected.
1 rows affected.


[(u'image_data_train', u'image_data_train_packed', u'y', u'x', u'smallint', [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 6250, 255.0, 10, [2, 3, 4, 5, 6, 7, 8, 9], [0, 1, 2, 3, 4, 5, 6, 7])]

Check distribution:

In [42]:
%%sql
SELECT __dist_key__, x_shape, y_shape, buffer_id FROM image_data_train_packed ORDER BY __dist_key__;

 * postgresql://gpadmin@localhost:8000/cifar_places
8 rows affected.


[(0, [6250, 32, 32, 3], [6250, 10], 1),
 (1, [6250, 32, 32, 3], [6250, 10], 4),
 (3, [6250, 32, 32, 3], [6250, 10], 7),
 (14, [6250, 32, 32, 3], [6250, 10], 6),
 (28, [6250, 32, 32, 3], [6250, 10], 5),
 (34, [6250, 32, 32, 3], [6250, 10], 0),
 (55, [6250, 32, 32, 3], [6250, 10], 3),
 (56, [6250, 32, 32, 3], [6250, 10], 2)]

<a id="pp_train2d"></a>
## 2d.  Segments on 1 segment

Now distribute 1 segment on a host with GPUs attached (if for some reason I need to do this):

In [43]:
%%sql
DROP TABLE IF EXISTS image_data_train_packed, image_data_train_packed_summary;

SELECT madlib.training_preprocessor_dl('image_data_train',          -- Source table
                                        'image_data_train_packed',  -- Output table
                                        'y',                        -- Dependent variable
                                        'x',                        -- Independent variable
                                        NULL,                       -- Buffer size
                                        255,                        -- Normalizing constant
                                        NULL,                       -- Number of classes
                                        'segments_to_use_1seg'      -- Distribution rules
                                        );
SELECT * FROM image_data_train_packed_summary;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
1 rows affected.
1 rows affected.


[(u'image_data_train', u'image_data_train_packed', u'y', u'x', u'smallint', [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 16667, 255.0, 10, [2], [0])]

Check distribution:

In [44]:
%%sql
SELECT __dist_key__, x_shape, y_shape, buffer_id FROM image_data_train_packed ORDER BY __dist_key__;

 * postgresql://gpadmin@localhost:8000/cifar_places
3 rows affected.


[(34, [16667, 32, 32, 3], [16667, 10], 1),
 (34, [16666, 32, 32, 3], [16666, 10], 2),
 (34, [16667, 32, 32, 3], [16667, 10], 0)]

<a id="pp_val"></a>
# 3.  Run preprocessor for validation image data

The same idea applies to the validation data set for distribution rules.  Continuing the example above with distribution to a single segment:

In [45]:
%%sql
DROP TABLE IF EXISTS image_data_val_packed, image_data_val_packed_summary;

SELECT madlib.validation_preprocessor_dl('image_data_val',           -- Source table
                                         'image_data_val_packed',    -- Output table
                                         'y',                        -- Dependent variable
                                         'x',                        -- Independent variable
                                         'image_data_train_packed',  -- Training preprocessor output table 
                                         NULL,                       -- Buffer size
                                         'segments_to_use_1seg'      -- Distribution rules
                                         );
SELECT * FROM image_data_val_packed_summary;

 * postgresql://gpadmin@localhost:8000/cifar_places
Done.
1 rows affected.
1 rows affected.


[(u'image_data_val', u'image_data_val_packed', u'y', u'x', u'smallint', [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 10000, 255.0, 10, [2], [0])]

Check distribution:

In [46]:
%%sql
SELECT __dist_key__, x_shape, y_shape, buffer_id FROM image_data_val_packed ORDER BY __dist_key__;

 * postgresql://gpadmin@localhost:8000/cifar_places
1 rows affected.


[(34, [10000, 32, 32, 3], [10000, 10], 0)]